In [2]:
import grpc
import tensorflow as tf
from tensorflow_serving.apis import predict_pb2, prediction_service_pb2_grpc

2025-02-21 01:53:15.659457: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [9]:
host="localhost:8500"
channel = grpc.insecure_channel(host)
stub = prediction_service_pb2_grpc.PredictionServiceStub(channel)
stub

In [10]:
from PIL import Image
import numpy as np

def read_image(path):
    with Image.open(path) as img:
        img = img.resize((299, 299), Image.NEAREST)
    return img

def preprocess_input(x):
    x = x / 127.5
    x -= 1.
    return x

img = read_image("/workspaces/k8deployment/data/test/skirt/0558b2c5-be00-49de-b27f-8c88114ac36f.jpg")
X = np.array(img)

In [11]:
X.shape
tf.make_tensor_proto(X, dtype=float, shape=X.shape)

dtype: DT_FLOAT
tensor_shape {
  dim {
    size: 299
  }
  dim {
    size: 299
  }
  dim {
    size: 3
  }
}
tensor_content: "\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000kC\000\000QC\000\0008C\000\000hC\000\000NC\000\0005C\000\000^C\000\000DC\000\000+C\000\000[C\000\000AC\000\000(C\000\000\\C\000\000BC\000\000)C\000\000`C\000\000FC\000\000-C\000\000bC\000\000HC\000\000/C\000\000fC\000\000LC\000\0003C\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000gC\000\000MC\000\0004C\000\000iC\000\000OC\000\0006C\000\000nC\000\000TC\000\000;C\000\000lC\000\000RC\000\0009C\000\000fC\000\000LC\000\0003C\000\000nC\000\000TC\000\000;C\000\000dC\000\000JC\000\0001C\000\000lC\000\000RC\000\0009C\000\000nC\000\000TC\000\000;C\000\000hC\000\000NC\000\0005C\000\000mC\000\000SC\000\000:C\000\000`C\000\000FC\000\000-C\000\000iC\000\000OC\000\0006C\000\000fC\000\000LC\000\0003C\000\000kC\000\000QC\000\0008C\000\000kC\000\000QC\000\0008C\000\000mC\000\000SC\000\000:C\00

In [12]:
pb_request = predict_pb2.PredictRequest()
pb_request.model_spec.name = "clothes-classifier"
pb_request.model_spec.signature_name = "serving_default"
pb_request.inputs['inputs'].CopyFrom(tf.make_tensor_proto(X, dtype=float, shape=X.shape))

pb_request

model_spec {
  name: "clothes-classifier"
  signature_name: "serving_default"
}
inputs {
  key: "inputs"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 299
      }
      dim {
        size: 299
      }
      dim {
        size: 3
      }
    }
    tensor_content: "\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000kC\000\000QC\000\0008C\000\000hC\000\000NC\000\0005C\000\000^C\000\000DC\000\000+C\000\000[C\000\000AC\000\000(C\000\000\\C\000\000BC\000\000)C\000\000`C\000\000FC\000\000-C\000\000bC\000\000HC\000\000/C\000\000fC\000\000LC\000\0003C\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000gC\000\000MC\000\0004C\000\000iC\000\000OC\000\0006C\000\000nC\000\000TC\000\000;C\000\000lC\000\000RC\000\0009C\000\000fC\000\000LC\000\0003C\000\000nC\000\000TC\000\000;C\000\000dC\000\000JC\000\0001C\000\000lC\000\000RC\000\0009C\000\000nC\000\000TC\000\000;C\000\000hC\000\000NC\000\0005C\000\000mC\000\000SC\000\000:C\000\000`C\000\0

In [13]:
pb_response = stub.Predict(pb_request, timeout=20.0)

_InactiveRpcError: <_InactiveRpcError of RPC that terminated with:
	status = StatusCode.FAILED_PRECONDITION
	details = "Could not find variable batch_normalization_9/moving_variance. This could mean that the variable has been deleted. In TF1, it can also mean the variable is uninitialized. Debug info: container=localhost, status error message=Resource localhost/batch_normalization_9/moving_variance/N10tensorflow3VarE does not exist.
	 [[{{function_node __inference_serving_default_3363}}{{node functional_1_1/xception_1/batch_normalization_9_1/Cast_1/ReadVariableOp}}]]"
	debug_error_string = "UNKNOWN:Error received from peer ipv4:127.0.0.1:8500 {grpc_message:"Could not find variable batch_normalization_9/moving_variance. This could mean that the variable has been deleted. In TF1, it can also mean the variable is uninitialized. Debug info: container=localhost, status error message=Resource localhost/batch_normalization_9/moving_variance/N10tensorflow3VarE does not exist.\n\t [[{{function_